# Imports and configs

In [26]:
from experiment.luna.luna_record_provider import LunaRecordProvider
from sziszapangma.integration.experiment_manager import ExperimentManager
from sziszapangma.integration.repository.multi_files_experiment_repository import MultiFilesExperimentRepository
from sziszapangma.integration.path_filter import ExtensionPathFilter
from pymongo import MongoClient
from spacy.tokens.doc import Doc
import pandas as pd
from experiment.voicelab.voicelab_telco_record_provider import VoicelabTelcoRecordProvider
from sziszapangma.integration.repository.experiment_repository import ExperimentRepository
from dataclasses import dataclass
import itertools
from typing import Optional, Any, List
import numpy as np

In [27]:
pd.set_option('display.max_rows', None)

# Load datasets and other pipeline objects

In [28]:
VOICELAB_DATASET_DIRECTORY = 'experiment_data/dataset/voicelab_cbiz_testset_20220322'
LUNA_DATASET_DIRECTORY = 'experiment_data/dataset/LUNA.PL'

In [29]:
## repository collections
GOLD_TRANSCRIPT = 'gold_transcript'
GOLD_TRANSCRIPT_SPACY = 'gold_transcript_spacy'

TECHMO_POLISH_ASR = 'techmo_polish_asr'
WORD_TECHMO_MERTICS_WER = 'word_techmo_metrics_wer'
WORD_TECHMO_ALIGNMENT_WER = 'word_techmo_alignment_wer'
TECHMO_SPACY = 'techmo_spacy'
POS_TECHMO_ALIGNMENT_WER = 'pos_techmo_alignment_wer'
POS_TECHMO_METRICS_WER = 'pos_techmo_metrics_wer'
TAG_SPACY_TECHMO_METRICS_WER_EMBEDDINGS = 'tag_spacy_techmo_metrics_wer_embeddings'
TAG_SPACY_TECHMO_ALIGNMENT_WER_EMBEDDINGS = 'tag_spacy_techmo_alignment_wer_embeddings'

AJN_POLISH_ASR = 'ajn_polish_asr'
WORD_AJN_MERTICS_WER = 'word_ajn_metrics_wer'
WORD_AJN_ALIGNMENT_WER = 'word_ajn_alignment_wer'
AJN_SPACY = 'ajn_spacy'
POS_AJN_ALIGNMENT_WER = 'pos_ajn_metrics_wer'
POS_AJN_METRICS_WER = 'pos_ajn_alignment_wer'
TAG_SPACY_AJN_METRICS_WER_EMBEDDINGS = 'tag_spacy_ajn_metrics_wer_embeddings'
TAG_SPACY_AJN_ALIGNMENT_WER_EMBEDDINGS = 'tag_spacy_ajn_alignment_wer_embeddings'

In [30]:
@dataclass
class CollectionsConfig:
    config_name: str
    gold_transcript: str
    gold_transcript_spacy: str
    asr: str
    word_asr_metric_wer: str
    word_asr_alignment_wer: str
    asr_spacy: str
    pos_asr_metric_wer: str
    pos_asr_alignment_wer: str
    tag_metric_wer: str
    tag_alignment_wer: str

In [31]:
techmo_connections_config = CollectionsConfig(
    config_name='TECHMO ASR',
    gold_transcript=GOLD_TRANSCRIPT,
    gold_transcript_spacy=GOLD_TRANSCRIPT_SPACY,
    asr=TECHMO_POLISH_ASR,
    word_asr_metric_wer=WORD_TECHMO_MERTICS_WER,
    word_asr_alignment_wer=WORD_TECHMO_ALIGNMENT_WER,
    asr_spacy=TECHMO_SPACY,
    pos_asr_metric_wer=POS_TECHMO_METRICS_WER,
    pos_asr_alignment_wer=POS_TECHMO_ALIGNMENT_WER,
    tag_metric_wer=TAG_SPACY_TECHMO_METRICS_WER_EMBEDDINGS,
    tag_alignment_wer=TAG_SPACY_TECHMO_ALIGNMENT_WER_EMBEDDINGS
)
ajn_connections_config = CollectionsConfig(
    config_name='AJN ASR',
    gold_transcript=GOLD_TRANSCRIPT,
    gold_transcript_spacy=GOLD_TRANSCRIPT_SPACY,
    asr=AJN_POLISH_ASR,
    word_asr_metric_wer=WORD_AJN_MERTICS_WER,
    word_asr_alignment_wer=WORD_AJN_ALIGNMENT_WER,
    asr_spacy=AJN_SPACY,
    pos_asr_metric_wer=POS_AJN_ALIGNMENT_WER,
    pos_asr_alignment_wer=POS_AJN_METRICS_WER,
    tag_metric_wer=TAG_SPACY_AJN_METRICS_WER_EMBEDDINGS,
    tag_alignment_wer=TAG_SPACY_AJN_ALIGNMENT_WER_EMBEDDINGS
)

In [32]:
voicelab_experiment_repository = MultiFilesExperimentRepository(
    'experiment_data/pipeline',
    'asr_benchmark_voicelab_cbiz_testset_20220322'
)
luna_experiment_repository = MultiFilesExperimentRepository(
    'experiment_data/pipeline',
    'asr_benchmark_luna'
)
print(f'voicelab examples count {len(voicelab_experiment_repository.get_all_record_ids())}')
print(f'luna examples count {len(luna_experiment_repository.get_all_record_ids())}')

voicelab examples count 800
luna examples count 500


In [33]:
voicelab_record_provider = VoicelabTelcoRecordProvider(ExtensionPathFilter(
    root_directory=VOICELAB_DATASET_DIRECTORY,
    extension='wav',
), relation_manager_root_path='experiment_data/dataset_relation_manager_data/voicelab_cbiz_testset_20220322')

luna_record_provider = LunaRecordProvider(ExtensionPathFilter(
    root_directory=f'{LUNA_DATASET_DIRECTORY}/LUNA.PL',
    extension='wav',
), relation_manager_root_path='experiment_data/dataset_relation_manager_data/luna')

In [34]:
# explore POS 
a = []
for record_id in list(luna_record_provider.get_all_records()):
    g = luna_experiment_repository.get_property_for_key(record_id, GOLD_TRANSCRIPT)
    # print(g)
    a.extend(list(set([it['pos'] for it in g])))
    # print(a)
# set(a)
# https://www.sketchengine.eu/polish-nkjp-part-of-speech-tagset/
# {'-': 'X',
#  'ADJc': 'ADJ',
#  'ADJp': 'ADJ',
#  'ADV': 'ADV',
#  'ADVn': 'ADV',
#  'CC',
#  'ITJ',
#  'NUM': 'NUM',
#  'NUMc': 'NUM',
#  'NUMp': 'NUM',
#  'NUMq': 'NUM',
#  'Nc',
#  'Np',
#  'PADJ',
#  'PART',
#  'PINT',
#  'PN',
#  'PPER',
#  'PQ',
#  'PREF',
#  'PREL',
#  'PreP',
#  'PrePF',
#  'PrePp',
#  'PropName',
#  'VA',
#  'VS',
#  'VV',
#  'acron'}

In [35]:
def get_gold_transcript_for(record_id: str, experiment_repository: ExperimentRepository, 
                            collections_config: CollectionsConfig) -> str:
    gold_trnascript_property = experiment_repository.get_property_for_key(
        record_id, collections_config.gold_transcript)
    return ' '.join([it['word'] for it in gold_trnascript_property])

def get_asr_transcript_for(record_id: str, experiment_repository: ExperimentRepository,
                           collections_config: CollectionsConfig) -> str:
    gold_trnascript_property = experiment_repository.get_property_for_key(record_id, collections_config.asr)
    return gold_trnascript_property['full_text']

def get_word_alignment_df(record_id: str, experiment_repository: ExperimentRepository, 
                        collections_config: CollectionsConfig) -> pd.DataFrame:
    word_alignment_wer = experiment_repository.get_property_for_key(record_id, 
                                                                    collections_config.word_asr_alignment_wer)
    arr = [
        {
            'step_type': it['step_type'],
            'reference_word_text': it['step_words']['reference_word']['text'] 
            if 'reference_word' in it['step_words'] else '',
            'hypothesis_word_text': it['step_words']['hypothesis_word']['text']
            if 'hypothesis_word' in it['step_words'] else '',
        }
        for it in word_alignment_wer
    ]
    return pd.DataFrame(arr)


def get_pos_alignment_df(record_id: str, experiment_repository: ExperimentRepository, 
                        collections_config: CollectionsConfig) -> pd.DataFrame:
    pos_alignment_wer = experiment_repository.get_property_for_key(record_id, 
                                                                   collections_config.pos_asr_alignment_wer)
    gold_transcript_spacy = experiment_repository.get_property_for_key(record_id,
                                                                       collections_config.gold_transcript_spacy)
    gold_trnascript_spacy_word_dict = {it['id']: it['word'] for it in gold_transcript_spacy}
    asr_spacy = experiment_repository.get_property_for_key(record_id, collections_config.asr_spacy)
    asr_spacy_word_dict = {it['id']: it['word'] for it in asr_spacy}
    arr = [
        {
            'step_type': it['step_type'],
            'reference_word_pos': it['step_words']['reference_word']['text'] 
            if 'reference_word' in it['step_words'] else '',
            'reference_word_text': gold_trnascript_spacy_word_dict[it['step_words']['reference_word']['id']] 
            if 'reference_word' in it['step_words'] else '',
            'hypothesis_word_pos': it['step_words']['hypothesis_word']['text']
            if 'hypothesis_word' in it['step_words'] else '',
            'hypothesis_word_text': asr_spacy_word_dict[it['step_words']['hypothesis_word']['id']] 
            if 'hypothesis_word' in it['step_words'] else ''
        }
        for it in pos_alignment_wer
    ]
    return pd.DataFrame(arr)



def get_tag_alignment_df(record_id: str, experiment_repository: ExperimentRepository, 
                        collections_config: CollectionsConfig) -> pd.DataFrame:
    word_alignment_wer = experiment_repository.get_property_for_key(record_id, 
                                                                    collections_config.tag_alignment_wer)
    arr = [
        {
            'step_type': it['step_type'],
            'reference_word_text': it['step_words']['reference_word']['text'] 
            if 'reference_word' in it['step_words'] else '',
            'hypothesis_word_text': it['step_words']['hypothesis_word']['text']
            if 'hypothesis_word' in it['step_words'] else '',
        }
        for it in word_alignment_wer
    ]
    return pd.DataFrame(arr)
    
    
def show_report_for(record_id: str, experiment_repository: ExperimentRepository,
                    collections_config: CollectionsConfig):
    print('record_id:', record_id)
    print('properties_confiog:', collections_config.config_name)
    print()
    print(f'gold transcript: {get_gold_transcript_for(record_id, experiment_repository, collections_config)}')    
    print()
    print(f'asr transcript: {get_asr_transcript_for(record_id, experiment_repository, collections_config)}')
    print()
    print(f"word wer {experiment_repository.get_property_for_key(record_id, collections_config.word_asr_metric_wer)}")
    print()
    print(f"pos wer {experiment_repository.get_property_for_key(record_id, collections_config.pos_asr_metric_wer)}")
    print()
    print(f"tag wer {experiment_repository.get_property_for_key(record_id, collections_config.tag_metric_wer)}")
    print()
    display(get_word_alignment_df(record_id, experiment_repository, collections_config))
    print()
    display(get_pos_alignment_df(record_id, experiment_repository, collections_config))
    print()
    display(get_tag_alignment_df(record_id, experiment_repository, collections_config))
    print('--------------------------------------------------------------')
    print('--------------------------------------------------------------')
    print('--------------------------------------------------------------')

# Report for LUNA and TECHMO ASR

In [36]:
for it in list(luna_record_provider.get_all_records())[:1]:
    show_report_for(it, luna_experiment_repository, techmo_connections_config)

record_id: LUNA.PL__JAKDOJECHAC__DOBRAJAKOSC__F__2_2007-03-26_12_22_36__2_2007-03-26_12_22_36
properties_confiog: TECHMO ASR

gold transcript: xxx dzień dobry dzień dobry proszę pana ja chciałam się dowiedzieć bo nie bardzo wiem gdzie znajduje się ulica Zwierzyniecka i jak dojechać z Bródna na przykład ? na Zwierzyniecką na Zwierzyniecką a z Bródna z którego miejsca ? z Bródna to jest ulica Wyszogrodzka tu przy Rembielińskiej czyli przy tramwajach tak ? przy tramwajach tak może pani poczeka sprawdzę dobrze dobrze pani sobie podjedzie tramwajem do Ronda Żaba tak od Ronda Żaba już sto sześćdziesiąt dwa jest sto sześćdziesiąt dwa tak i sto sześćdziesiąt dwa tam dojadę do tej ulicy tak może pani wysiąść na przystanku Bartycka albo Sielce Bartycka albo ? Sielce Sielce tak ? tak aha i tam w pobliżu jest ta ulica tak ? a Zwierzyniecka wysoki numer ma pani ? Zwierzyniecka zaraz momencik osiem A Zwierzyniecka to to przy Sielce trza wysiąść przy Sielce tak ? tak przystanek Sielce aha tak no dobr

step_type reference_word_text hypothesis_word_text
0        DELETION                 xxx                     
1         CORRECT               dzień                dzień
2         CORRECT               dobry                dobry
3         CORRECT               dzień                dzień
4         CORRECT               dobry                dobry
5         CORRECT              proszę               proszę
6         CORRECT                pana                 pana
7         CORRECT                  ja                   ja
8         CORRECT            chciałam             chciałam
9         CORRECT                 się                  się
10        CORRECT          dowiedzieć           dowiedzieć
11        CORRECT                  bo                   bo
12        CORRECT                 nie                  nie
13        CORRECT              bardzo               bardzo
14        CORRECT                wiem                 wiem
15        CORRECT               gdzie                gdzie
16        CORRECT            znajduje             znajduje
17        CORRECT                 się                  się
18        CORRECT               ulica                ulica
19   SUBSTITUTION       Zwierzyniecka        zwierzyniecka
20        CORRECT                   i                    i
21        CORRECT                 jak                  jak
22        CORRECT            dojechać             dojechać
23        CORRECT                   z                    z
24       DELETION              Bródna                     
25       DELETION                  na                     
26       DELETION            przykład                     
27   SUBSTITUTION                   ?               bródna
28        CORRECT                  na                   na
29   SUBSTITUTION       Zwierzyniecką        zwierzyniecką
30        CORRECT                  na                   na
31   SUBSTITUTION       Zwierzyniecką        zwierzyniecką
32   SUBSTITUTION                   a                   ja
33        CORRECT                   z                    z
34   SUBSTITUTION              Bródna               bródna
35        CORRECT                   z                    z
36        CORRECT             którego              którego
37        CORRECT             miejsca              miejsca
38       DELETION                   ?                     
39        CORRECT                   z                    z
40   SUBSTITUTION              Bródna               bródna
41        CORRECT                  to                   to
42        CORRECT                jest                 jest
43        CORRECT               ulica                ulica
44   SUBSTITUTION        Wyszogrodzka         wyszogrodzka
45        CORRECT                  tu                   tu
46        CORRECT                przy                 przy
47   SUBSTITUTION      Rembielińskiej       rembielińskiej
48        CORRECT               czyli                czyli
49        CORRECT                przy                 przy
50        CORRECT          tramwajach           tramwajach
51       DELETION                 tak                     
52       DELETION                   ?                     
53        CORRECT                przy                 przy
54        CORRECT          tramwajach           tramwajach
55        CORRECT                 tak                  tak
56        CORRECT                może                 może
57       DELETION                pani                     
58       DELETION             poczeka                     
59        CORRECT            sprawdzę             sprawdzę
60        CORRECT              dobrze               dobrze
61        CORRECT              dobrze               dobrze
62       DELETION                pani                     
63       DELETION               sobie                     
64        CORRECT           podjedzie            podjedzie
65        CORRECT           tramwajem            tramwajem
66        CORRECT                  do                  

step_type reference_word_pos reference_word_text hypothesis_word_pos  \
0        DELETION               PRON                 xxx                       
1         CORRECT               NOUN               dzień                NOUN   
2         CORRECT                ADJ               dobry                 ADJ   
3         CORRECT               NOUN               dzień                NOUN   
4         CORRECT                ADJ               dobry                 ADJ   
5         CORRECT               VERB              proszę                VERB   
6         CORRECT               NOUN                pana                NOUN   
7         CORRECT               PRON                  ja                PRON   
8         CORRECT               VERB            chciałam                VERB   
9         CORRECT               PRON                 się                PRON   
10        CORRECT               VERB          dowiedzieć                VERB   
11        CORRECT              SCONJ                  bo               SCONJ   
12        CORRECT               PART                 nie                PART   
13        CORRECT                ADV              bardzo                 ADV   
14        CORRECT               VERB                wiem                VERB   
15        CORRECT                ADV               gdzie                 ADV   
16        CORRECT               VERB            znajduje                VERB   
17        CORRECT               PRON                 się                PRON   
18        CORRECT               NOUN               ulica                NOUN   
19        CORRECT                ADJ       Zwierzyniecka                 ADJ   
20        CORRECT              CCONJ                   i               CCONJ   
21        CORRECT                ADV                 jak                 ADV   
22        CORRECT               VERB            dojechać                VERB   
23       DELETION                ADP                   z                       
24       DELETION              PROPN              Bródna                       
25        CORRECT                ADP                  na                 ADP   
26        CORRECT               NOUN            przykład                NOUN   
27       DELETION              PUNCT                   ?                       
28        CORRECT                ADP                  na                 ADP   
29        CORRECT              PROPN       Zwierzyniecką               PROPN   
30        CORRECT                ADP                  na                 ADP   
31        CORRECT              PROPN       Zwierzyniecką               PROPN   
32   SUBSTITUTION              CCONJ                   a                PRON   
33        CORRECT                ADP                   z                 ADP   
34   SUBSTITUTION              PROPN              Bródna                NOUN   
35        CORRECT                ADP                   z                 ADP   
36        CORRECT                DET             którego                 DET   
37        CORRECT               NOUN             miejsca                NOUN   
38       DELETION              PUNCT                   ?                       
39        CORRECT                ADP                   z                 ADP   
40   SUBSTITUTION              PROPN              Bródna                NOUN   
41        CORRECT                AUX                  to                 AUX   
42        CORRECT                AUX                jest                 AUX   
43        CORRECT               NOUN               ulica                NOUN   
44   SUBSTITUTION              PROPN        Wyszogrodzka                 ADJ   
45        CORRECT                ADV                  tu                 ADV   
46        CORRECT                ADP                przy                 ADP   
47   SUBSTITUTION              PROPN      Rembielińskiej                 ADJ   
48        CORRECT              CCONJ               czyli               CCONJ   
49      

step_type reference_word_text hypothesis_word_text
0        DELETION                 xxx                     
1         CORRECT               dzień                dzień
2         CORRECT               dobry                dobry
3         CORRECT               dzień                dzień
4         CORRECT               dobry                dobry
5         CORRECT              proszę               proszę
6         CORRECT                pana                 pana
7         CORRECT                  ja                   ja
8         CORRECT            chciałam             chciałam
9         CORRECT                 się                  się
10        CORRECT          dowiedzieć           dowiedzieć
11        CORRECT                  bo                   bo
12        CORRECT                 nie                  nie
13        CORRECT              bardzo               bardzo
14        CORRECT                wiem                 wiem
15        CORRECT               gdzie                gdzie
16        CORRECT            znajduje             znajduje
17        CORRECT                 się                  się
18        CORRECT               ulica                ulica
19   SUBSTITUTION       Zwierzyniecka        zwierzyniecka
20        CORRECT                   i                    i
21        CORRECT                 jak                  jak
22        CORRECT            dojechać             dojechać
23        CORRECT                   z                    z
24       DELETION              Bródna                     
25       DELETION                  na                     
26       DELETION            przykład                     
27   SUBSTITUTION                   ?               bródna
28        CORRECT                  na                   na
29   SUBSTITUTION       Zwierzyniecką        zwierzyniecką
30        CORRECT                  na                   na
31   SUBSTITUTION       Zwierzyniecką        zwierzyniecką
32   SUBSTITUTION                   a                   ja
33        CORRECT                   z                    z
34   SUBSTITUTION              Bródna               bródna
35        CORRECT                   z                    z
36        CORRECT             którego              którego
37        CORRECT             miejsca              miejsca
38       DELETION                   ?                     
39        CORRECT                   z                    z
40   SUBSTITUTION              Bródna               bródna
41        CORRECT                  to                   to
42        CORRECT                jest                 jest
43        CORRECT               ulica                ulica
44   SUBSTITUTION        Wyszogrodzka         wyszogrodzka
45        CORRECT                  tu                   tu
46        CORRECT                przy                 przy
47   SUBSTITUTION      Rembielińskiej       rembielińskiej
48        CORRECT               czyli                czyli
49        CORRECT                przy                 przy
50        CORRECT          tramwajach           tramwajach
51       DELETION                 tak                     
52       DELETION                   ?                     
53        CORRECT                przy                 przy
54        CORRECT          tramwajach           tramwajach
55        CORRECT                 tak                  tak
56        CORRECT                może                 może
57       DELETION                pani                     
58       DELETION             poczeka                     
59        CORRECT            sprawdzę             sprawdzę
60        CORRECT              dobrze               dobrze
61        CORRECT              dobrze               dobrze
62       DELETION                pani                     
63       DELETION               sobie                     
64        CORRECT           podjedzie            podjedzie
65        CORRECT           tramwajem            tramwajem
66        CORRECT                  do                  

--------------------------------------------------------------
--------------------------------------------------------------
--------------------------------------------------------------


# Report for LUNA and AJN ASR

In [37]:
for it in list(luna_record_provider.get_all_records())[:1]:
    show_report_for(it, luna_experiment_repository, ajn_connections_config)

record_id: LUNA.PL__JAKDOJECHAC__DOBRAJAKOSC__F__2_2007-03-26_12_22_36__2_2007-03-26_12_22_36
properties_confiog: AJN ASR

gold transcript: xxx dzień dobry dzień dobry proszę pana ja chciałam się dowiedzieć bo nie bardzo wiem gdzie znajduje się ulica Zwierzyniecka i jak dojechać z Bródna na przykład ? na Zwierzyniecką na Zwierzyniecką a z Bródna z którego miejsca ? z Bródna to jest ulica Wyszogrodzka tu przy Rembielińskiej czyli przy tramwajach tak ? przy tramwajach tak może pani poczeka sprawdzę dobrze dobrze pani sobie podjedzie tramwajem do Ronda Żaba tak od Ronda Żaba już sto sześćdziesiąt dwa jest sto sześćdziesiąt dwa tak i sto sześćdziesiąt dwa tam dojadę do tej ulicy tak może pani wysiąść na przystanku Bartycka albo Sielce Bartycka albo ? Sielce Sielce tak ? tak aha i tam w pobliżu jest ta ulica tak ? a Zwierzyniecka wysoki numer ma pani ? Zwierzyniecka zaraz momencik osiem A Zwierzyniecka to to przy Sielce trza wysiąść przy Sielce tak ? tak przystanek Sielce aha tak no dobrze 

step_type reference_word_text hypothesis_word_text
0        DELETION                 xxx                     
1        DELETION               dzień                     
2        DELETION               dobry                     
3        DELETION               dzień                     
4        DELETION               dobry                     
5    SUBSTITUTION              proszę             niedobre
6    SUBSTITUTION                pana                   n.
7    SUBSTITUTION                  ja                   e.
8    SUBSTITUTION            chciałam                pracy
9    SUBSTITUTION                 się                    a
10   SUBSTITUTION          dowiedzieć                   to
11   SUBSTITUTION                  bo                długo
12        CORRECT                 nie                  nie
13   SUBSTITUTION              bardzo                 było
14   SUBSTITUTION                wiem                   to
15   SUBSTITUTION               gdzie              dziecko
16   SUBSTITUTION            znajduje                czuje
17        CORRECT                 się                  się
18       DELETION               ulica                     
19   SUBSTITUTION       Zwierzyniecka               równie
20   SUBSTITUTION                   i               szybko
21        CORRECT                 jak                  jak
22       DELETION            dojechać                     
23       DELETION                   z                     
24       DELETION              Bródna                     
25       DELETION                  na                     
26   SUBSTITUTION            przykład                   to
27   SUBSTITUTION                   ?                cecha
28   SUBSTITUTION                  na                 brud
29   SUBSTITUTION       Zwierzyniecką                   ta
30        CORRECT                  na                   na
31       DELETION       Zwierzyniecką                     
32       DELETION                   a                     
33       DELETION                   z                     
34   SUBSTITUTION              Bródna             przykład
35   SUBSTITUTION                   z                  się
36   SUBSTITUTION             którego             ostatnio
37   SUBSTITUTION             miejsca         inżynierowie
38   SUBSTITUTION                   ?                    i
39   SUBSTITUTION                   z               brudno
40   SUBSTITUTION              Bródna           straszliwy
41   SUBSTITUTION                  to                 szok
42   SUBSTITUTION                jest            brodatego
43        CORRECT               ulica                ulica
44       DELETION        Wyszogrodzka                     
45   SUBSTITUTION                  tu         wyszogrodzka
46        CORRECT                przy                 przy
47       DELETION      Rembielińskiej                     
48       DELETION               czyli                     
49   SUBSTITUTION                przy       rembielińskiej
50   SUBSTITUTION          tramwajach                  ich
51   SUBSTITUTION                 tak               cztero
52   SUBSTITUTION                   ?                  oto
53   SUBSTITUTION                przy                   ta
54   SUBSTITUTION          tramwajach                  jak
55        CORRECT                 tak                  tak
56       DELETION                może                     
57       DELETION                pani                     
58       DELETION             poczeka                     
59   SUBSTITUTION            sprawdzę                 dużo
60   SUBSTITUTION              dobrze              punktów
61   SUBSTITUTION              dobrze                <unk>
62   SUBSTITUTION                pani                  oni
63   SUBSTITUTION               sobie                 żeby
64   SUBSTITUTION           podjedzie              podróży
65        CORRECT           tramwajem            tramwajem
66        CORRECT                  do                  

step_type reference_word_pos reference_word_text hypothesis_word_pos  \
0        DELETION               PRON                 xxx                       
1        DELETION               NOUN               dzień                       
2         CORRECT                ADJ               dobry                 ADJ   
3    SUBSTITUTION               NOUN               dzień                   X   
4    SUBSTITUTION                ADJ               dobry               PUNCT   
5    SUBSTITUTION               VERB              proszę                   X   
6    SUBSTITUTION               NOUN                pana               PUNCT   
7    SUBSTITUTION               PRON                  ja                NOUN   
8    SUBSTITUTION               VERB            chciałam               CCONJ   
9         CORRECT               PRON                 się                PRON   
10       DELETION               VERB          dowiedzieć                       
11   SUBSTITUTION              SCONJ                  bo                 ADV   
12        CORRECT               PART                 nie                PART   
13   SUBSTITUTION                ADV              bardzo                 AUX   
14   SUBSTITUTION               VERB                wiem                 DET   
15   SUBSTITUTION                ADV               gdzie                NOUN   
16        CORRECT               VERB            znajduje                VERB   
17        CORRECT               PRON                 się                PRON   
18       DELETION               NOUN               ulica                       
19       DELETION                ADJ       Zwierzyniecka                       
20       DELETION              CCONJ                   i                       
21        CORRECT                ADV                 jak                 ADV   
22   SUBSTITUTION               VERB            dojechać                 ADV   
23   SUBSTITUTION                ADP                   z               SCONJ   
24   SUBSTITUTION              PROPN              Bródna                 AUX   
25   SUBSTITUTION                ADP                  na                NOUN   
26        CORRECT               NOUN            przykład                NOUN   
27   SUBSTITUTION              PUNCT                   ?                 DET   
28        CORRECT                ADP                  na                 ADP   
29      INSERTION                                                       NOUN   
30   SUBSTITUTION              PROPN       Zwierzyniecką                PRON   
31   SUBSTITUTION                ADP                  na                 ADV   
32   SUBSTITUTION              PROPN       Zwierzyniecką                NOUN   
33        CORRECT              CCONJ                   a               CCONJ   
34   SUBSTITUTION                ADP                   z                 ADV   
35   SUBSTITUTION              PROPN              Bródna                 ADJ   
36   SUBSTITUTION                ADP                   z                NOUN   
37   SUBSTITUTION                DET             którego                 ADJ   
38        CORRECT               NOUN             miejsca                NOUN   
39   SUBSTITUTION              PUNCT                   ?                 ADJ   
40        CORRECT                ADP                   z                 ADP   
41       DELETION              PROPN              Bródna                       
42       DELETION                AUX                  to                       
43   SUBSTITUTION                AUX                jest                 ADJ   
44   SUBSTITUTION               NOUN               ulica                PRON   
45   SUBSTITUTION              PROPN        Wyszogrodzka                 ADJ   
46   SUBSTITUTION                ADV                  tu                PART   
47   SUBSTITUTION                ADP                przy                 DET   
48   SUBSTITUTION              PROPN      Rembielińskiej               SCONJ   
49   SUB

step_type reference_word_text hypothesis_word_text
0        DELETION                 xxx                     
1        DELETION               dzień                     
2        DELETION               dobry                     
3    SUBSTITUTION               dzień             niedobre
4    SUBSTITUTION               dobry                    n
5    SUBSTITUTION              proszę                    .
6    SUBSTITUTION                pana                    e
7    SUBSTITUTION                  ja                    .
8    SUBSTITUTION            chciałam                pracy
9    SUBSTITUTION                 się                    a
10   SUBSTITUTION          dowiedzieć                   to
11   SUBSTITUTION                  bo                długo
12        CORRECT                 nie                  nie
13   SUBSTITUTION              bardzo                 było
14   SUBSTITUTION                wiem                   to
15   SUBSTITUTION               gdzie              dziecko
16   SUBSTITUTION            znajduje                czuje
17        CORRECT                 się                  się
18       DELETION               ulica                     
19   SUBSTITUTION       Zwierzyniecka               równie
20   SUBSTITUTION                   i               szybko
21        CORRECT                 jak                  jak
22       DELETION            dojechać                     
23       DELETION                   z                     
24       DELETION              Bródna                     
25       DELETION                  na                     
26   SUBSTITUTION            przykład                   to
27   SUBSTITUTION                   ?                cecha
28   SUBSTITUTION                  na                 brud
29   SUBSTITUTION       Zwierzyniecką                   ta
30        CORRECT                  na                   na
31       DELETION       Zwierzyniecką                     
32       DELETION                   a                     
33       DELETION                   z                     
34   SUBSTITUTION              Bródna             przykład
35   SUBSTITUTION                   z                  się
36   SUBSTITUTION             którego             ostatnio
37   SUBSTITUTION             miejsca         inżynierowie
38   SUBSTITUTION                   ?                    i
39   SUBSTITUTION                   z               brudno
40   SUBSTITUTION              Bródna           straszliwy
41   SUBSTITUTION                  to                 szok
42   SUBSTITUTION                jest            brodatego
43        CORRECT               ulica                ulica
44       DELETION        Wyszogrodzka                     
45   SUBSTITUTION                  tu         wyszogrodzka
46        CORRECT                przy                 przy
47       DELETION      Rembielińskiej                     
48       DELETION               czyli                     
49   SUBSTITUTION                przy       rembielińskiej
50   SUBSTITUTION          tramwajach                  ich
51   SUBSTITUTION                 tak               cztero
52   SUBSTITUTION                   ?                  oto
53   SUBSTITUTION                przy                   ta
54   SUBSTITUTION          tramwajach                  jak
55        CORRECT                 tak                  tak
56       DELETION                może                     
57   SUBSTITUTION                pani                 dużo
58   SUBSTITUTION             poczeka              punktów
59   SUBSTITUTION            sprawdzę                    <
60   SUBSTITUTION              dobrze                  unk
61   SUBSTITUTION              dobrze                    >
62   SUBSTITUTION                pani                  oni
63   SUBSTITUTION               sobie                 żeby
64   SUBSTITUTION           podjedzie              podróży
65        CORRECT           tramwajem            tramwajem
66        CORRECT                  do                  

--------------------------------------------------------------
--------------------------------------------------------------
--------------------------------------------------------------


# Report for VOICELAB and TECHMO ASR

In [38]:
for it in list(voicelab_record_provider.get_all_records())[:1]:
    show_report_for(it, voicelab_experiment_repository, techmo_connections_config)

record_id: wypozyczalnia__cbiz_tc_5492.agnt
properties_confiog: TECHMO ASR

gold transcript: dzień dobry nazywam się dorota pawłowska dzwonię z wypożyczalni samochodów auto dwadzieścia cztery czy rozmawiam z panem arturem drzewieckim dzień dobry panu bardzo mi miło dzwonię do pana w związku z ostatnim wypożyczeniem jednego z naszych samochodów na terenie holandii w rotterdamie czy potwierdza pan że korzystał pan z usług wynajmu w tym miejscu mmh już wszystko mówię natomiast w ramach formalności i potwierdzenia pańskiej tożsamości pozwoli pan że jeszcze tylko zadam kilka dodatkowych pytań żeby upewnić się że informacje które mam do przekazania trafią do właściwej osoby na początku bym poprosiła pana o podanie daty wynajmu auta w rotterdamie to oczywiście nie musi być dokładna dzienna data wystarczy miesiąc i który to był tydzień tego miesiąca bardzo panu dziękuję dobrze to poproszę pana jeszcze o podanie czterech ostatnich cyfr z numeru karty którą opłacał pan rezerwację cztery ostatnie

step_type        reference_word_text hypothesis_word_text
0         CORRECT                      dzień                dzień
1         CORRECT                      dobry                dobry
2         CORRECT                    nazywam              nazywam
3         CORRECT                        się                  się
4         CORRECT                     dorota               dorota
5         CORRECT                  pawłowska            pawłowska
6         CORRECT                    dzwonię              dzwonię
7         CORRECT                          z                    z
8         CORRECT               wypożyczalni         wypożyczalni
9         CORRECT                 samochodów           samochodów
10        CORRECT                       auto                 auto
11       DELETION                dwadzieścia                     
12   SUBSTITUTION                     cztery                   24
13        CORRECT                        czy                  czy
14        CORRECT                  rozmawiam            rozmawiam
15        CORRECT                          z                    z
16        CORRECT                      panem                panem
17        CORRECT                    arturem              arturem
18        CORRECT                drzewieckim          drzewieckim
19        CORRECT                      dzień                dzień
20        CORRECT                      dobry                dobry
21        CORRECT                       panu                 panu
22        CORRECT                     bardzo               bardzo
23        CORRECT                         mi                   mi
24        CORRECT                       miło                 miło
25        CORRECT                    dzwonię              dzwonię
26        CORRECT                         do                   do
27        CORRECT                       pana                 pana
28        CORRECT                          w                    w
29        CORRECT                    związku              związku
30        CORRECT                          z                    z
31        CORRECT                   ostatnim             ostatnim
32        CORRECT              wypożyczeniem        wypożyczeniem
33        CORRECT                    jednego              jednego
34        CORRECT                          z                    z
35        CORRECT                    naszych              naszych
36        CORRECT                 samochodów           samochodów
37        CORRECT                         na                   na
38        CORRECT                    terenie              terenie
39        CORRECT                   holandii             holandii
40        CORRECT                          w                    w
41        CORRECT                rotterdamie          rotterdamie
42       DELETION                        czy                     
43   SUBSTITUTION                 potwierdza                  wie
44        CORRECT                        pan                  pan
45        CORRECT                         że                   że
46        CORRECT                  korzystał            korzystał
47        CORRECT                        pan                  pan
48        CORRECT                          z                    z
49        CORRECT                      usług                usług
50        CORRECT                    wynajmu              wynajmu
51        CORRECT                          w                    w
52        CORRECT                        tym                  tym
53        CORRECT                    miejscu              miejscu
54   SUBSTITUTION                        mmh                  aha
55        CORRECT                        już                  już
56        CORRECT                   wszystko             wszystko
57        CORRECT                      mówię                mówię
58        CORRECT                  natomiast            natomiast
59        CORRECT                          w    

step_type reference_word_pos        reference_word_text  \
0         CORRECT               NOUN                      dzień   
1         CORRECT                ADJ                      dobry   
2         CORRECT               VERB                    nazywam   
3         CORRECT               PRON                        się   
4         CORRECT              PROPN                     dorota   
5         CORRECT                ADJ                  pawłowska   
6         CORRECT               VERB                    dzwonię   
7         CORRECT                ADP                          z   
8         CORRECT               NOUN               wypożyczalni   
9         CORRECT               NOUN                 samochodów   
10        CORRECT               NOUN                       auto   
11       DELETION                NUM                dwadzieścia   
12   SUBSTITUTION              PROPN                     cztery   
13        CORRECT              CCONJ                        czy   
14        CORRECT               VERB                  rozmawiam   
15        CORRECT                ADP                          z   
16        CORRECT               NOUN                      panem   
17        CORRECT              PROPN                    arturem   
18        CORRECT                ADJ                drzewieckim   
19        CORRECT               NOUN                      dzień   
20        CORRECT                ADJ                      dobry   
21        CORRECT               NOUN                       panu   
22        CORRECT                ADV                     bardzo   
23        CORRECT               PRON                         mi   
24        CORRECT                ADV                       miło   
25        CORRECT               VERB                    dzwonię   
26        CORRECT                ADP                         do   
27        CORRECT               NOUN                       pana   
28        CORRECT                ADP                          w   
29        CORRECT               NOUN                    związku   
30        CORRECT                ADP                          z   
31        CORRECT                ADJ                   ostatnim   
32        CORRECT               NOUN              wypożyczeniem   
33        CORRECT                ADJ                    jednego   
34        CORRECT                ADP                          z   
35        CORRECT                DET                    naszych   
36        CORRECT               NOUN                 samochodów   
37        CORRECT                ADP                         na   
38        CORRECT               NOUN                    terenie   
39        CORRECT              PROPN                   holandii   
40        CORRECT                ADP                          w   
41        CORRECT               NOUN                rotterdamie   
42       DELETION              CCONJ                        czy   
43        CORRECT               VERB                 potwierdza   
44        CORRECT               NOUN                        pan   
45        CORRECT              SCONJ                         że   
46        CORRECT               VERB                  korzystał   
47        CORRECT               NOUN                        pan   
48        CORRECT                ADP                          z   
49        CORRECT               NOUN                      usług   
50        CORRECT               NOUN                    wynajmu   
51        CORRECT                ADP                          w   
52        CORRECT                DET                        tym   
53        CORRECT               NOUN                    miejscu   
54   SUBSTITUTION                ADV                        mmh   
55        CORRECT               PART                        już   
56        CORRECT               PRON                   wszystko   
57        CORRECT               VERB                      mówię   
58        CORRECT              CCONJ                  n

step_type        reference_word_text hypothesis_word_text
0         CORRECT                      dzień                dzień
1         CORRECT                      dobry                dobry
2         CORRECT                    nazywam              nazywam
3         CORRECT                        się                  się
4         CORRECT                     dorota               dorota
5         CORRECT                  pawłowska            pawłowska
6         CORRECT                    dzwonię              dzwonię
7         CORRECT                          z                    z
8         CORRECT               wypożyczalni         wypożyczalni
9         CORRECT                 samochodów           samochodów
10        CORRECT                       auto                 auto
11       DELETION                dwadzieścia                     
12   SUBSTITUTION                     cztery                   24
13        CORRECT                        czy                  czy
14        CORRECT                  rozmawiam            rozmawiam
15        CORRECT                          z                    z
16        CORRECT                      panem                panem
17        CORRECT                    arturem              arturem
18        CORRECT                drzewieckim          drzewieckim
19        CORRECT                      dzień                dzień
20        CORRECT                      dobry                dobry
21        CORRECT                       panu                 panu
22        CORRECT                     bardzo               bardzo
23        CORRECT                         mi                   mi
24        CORRECT                       miło                 miło
25        CORRECT                    dzwonię              dzwonię
26        CORRECT                         do                   do
27        CORRECT                       pana                 pana
28        CORRECT                          w                    w
29        CORRECT                    związku              związku
30        CORRECT                          z                    z
31        CORRECT                   ostatnim             ostatnim
32        CORRECT              wypożyczeniem        wypożyczeniem
33        CORRECT                    jednego              jednego
34        CORRECT                          z                    z
35        CORRECT                    naszych              naszych
36        CORRECT                 samochodów           samochodów
37        CORRECT                         na                   na
38        CORRECT                    terenie              terenie
39        CORRECT                   holandii             holandii
40        CORRECT                          w                    w
41        CORRECT                rotterdamie          rotterdamie
42       DELETION                        czy                     
43   SUBSTITUTION                 potwierdza                  wie
44        CORRECT                        pan                  pan
45        CORRECT                         że                   że
46        CORRECT                  korzystał            korzystał
47        CORRECT                        pan                  pan
48        CORRECT                          z                    z
49        CORRECT                      usług                usług
50        CORRECT                    wynajmu              wynajmu
51        CORRECT                          w                    w
52        CORRECT                        tym                  tym
53        CORRECT                    miejscu              miejscu
54   SUBSTITUTION                        mmh                  aha
55        CORRECT                        już                  już
56        CORRECT                   wszystko             wszystko
57        CORRECT                      mówię                mówię
58        CORRECT                  natomiast            natomiast
59        CORRECT                          w    

--------------------------------------------------------------
--------------------------------------------------------------
--------------------------------------------------------------


In [39]:
for it in list(voicelab_record_provider.get_all_records())[:1]:
    show_report_for(it, voicelab_experiment_repository, ajn_connections_config)

record_id: wypozyczalnia__cbiz_tc_5492.agnt
properties_confiog: AJN ASR

gold transcript: dzień dobry nazywam się dorota pawłowska dzwonię z wypożyczalni samochodów auto dwadzieścia cztery czy rozmawiam z panem arturem drzewieckim dzień dobry panu bardzo mi miło dzwonię do pana w związku z ostatnim wypożyczeniem jednego z naszych samochodów na terenie holandii w rotterdamie czy potwierdza pan że korzystał pan z usług wynajmu w tym miejscu mmh już wszystko mówię natomiast w ramach formalności i potwierdzenia pańskiej tożsamości pozwoli pan że jeszcze tylko zadam kilka dodatkowych pytań żeby upewnić się że informacje które mam do przekazania trafią do właściwej osoby na początku bym poprosiła pana o podanie daty wynajmu auta w rotterdamie to oczywiście nie musi być dokładna dzienna data wystarczy miesiąc i który to był tydzień tego miesiąca bardzo panu dziękuję dobrze to poproszę pana jeszcze o podanie czterech ostatnich cyfr z numeru karty którą opłacał pan rezerwację cztery ostatnie cy

step_type        reference_word_text  \
0        DELETION                      dzień   
1        DELETION                      dobry   
2        DELETION                    nazywam   
3        DELETION                        się   
4        DELETION                     dorota   
5        DELETION                  pawłowska   
6        DELETION                    dzwonię   
7        DELETION                          z   
8        DELETION               wypożyczalni   
9        DELETION                 samochodów   
10       DELETION                       auto   
11       DELETION                dwadzieścia   
12       DELETION                     cztery   
13       DELETION                        czy   
14       DELETION                  rozmawiam   
15       DELETION                          z   
16       DELETION                      panem   
17       DELETION                    arturem   
18       DELETION                drzewieckim   
19       DELETION                      dzień   
20       DELETION                      dobry   
21       DELETION                       panu   
22       DELETION                     bardzo   
23       DELETION                         mi   
24       DELETION                       miło   
25       DELETION                    dzwonię   
26       DELETION                         do   
27       DELETION                       pana   
28       DELETION                          w   
29       DELETION                    związku   
30       DELETION                          z   
31       DELETION                   ostatnim   
32       DELETION              wypożyczeniem   
33       DELETION                    jednego   
34       DELETION                          z   
35       DELETION                    naszych   
36       DELETION                 samochodów   
37       DELETION                         na   
38       DELETION                    terenie   
39       DELETION                   holandii   
40       DELETION                          w   
41       DELETION                rotterdamie   
42       DELETION                        czy   
43       DELETION                 potwierdza   
44       DELETION                        pan   
45       DELETION                         że   
46       DELETION                  korzystał   
47       DELETION                        pan   
48       DELETION                          z   
49       DELETION                      usług   
50       DELETION                    wynajmu   
51       DELETION                          w   
52       DELETION                        tym   
53       DELETION                    miejscu   
54       DELETION                        mmh   
55       DELETION                        już   
56       DELETION                   wszystko   
57       DELETION                      mówię   
58       DELETION                  natomiast   
59       DELETION                          w   
60       DELETION                     ramach   
61       DELETION                formalności   
62       DELETION                          i   
63       DELETION              potwierdzenia   
64       DELETION                   pańskiej   
65       DELETION                 tożsamości   
66       DELETION                    pozwoli   
67       DELETION                        pan   
68       DELETION                         że   
69       DELETION                    jeszcze   
70       DELETION                      tylko   
71       DELETION                      zadam   
72       DELETION                      kilka   
73       DELETION                dodatkowych   
74       DELETION                      pytań   
75       DELETION                       żeby   
76       DELETION                    upewnić   
77       DELETION                        się   
78       DELETION                         że   
79       DELETION                 informacje   
80       DELETION                      które   
81       DELETION                        mam   
82       DELETION       

step_type reference_word_pos        reference_word_text  \
0        DELETION               NOUN                      dzień   
1        DELETION                ADJ                      dobry   
2    SUBSTITUTION               VERB                    nazywam   
3    SUBSTITUTION               PRON                        się   
4    SUBSTITUTION              PROPN                     dorota   
5         CORRECT                ADJ                  pawłowska   
6    SUBSTITUTION               VERB                    dzwonię   
7         CORRECT                ADP                          z   
8    SUBSTITUTION               NOUN               wypożyczalni   
9    SUBSTITUTION               NOUN                 samochodów   
10        CORRECT               NOUN                       auto   
11       DELETION                NUM                dwadzieścia   
12       DELETION              PROPN                     cztery   
13        CORRECT              CCONJ                        czy   
14   SUBSTITUTION               VERB                  rozmawiam   
15        CORRECT                ADP                          z   
16   SUBSTITUTION               NOUN                      panem   
17   SUBSTITUTION              PROPN                    arturem   
18        CORRECT                ADJ                drzewieckim   
19        CORRECT               NOUN                      dzień   
20        CORRECT                ADJ                      dobry   
21        CORRECT               NOUN                       panu   
22       DELETION                ADV                     bardzo   
23   SUBSTITUTION               PRON                         mi   
24        CORRECT                ADV                       miło   
25   SUBSTITUTION               VERB                    dzwonię   
26   SUBSTITUTION                ADP                         do   
27        CORRECT               NOUN                       pana   
28   SUBSTITUTION                ADP                          w   
29        CORRECT               NOUN                    związku   
30        CORRECT                ADP                          z   
31      INSERTION                                                 
32   SUBSTITUTION                ADJ                   ostatnim   
33        CORRECT               NOUN              wypożyczeniem   
34        CORRECT                ADJ                    jednego   
35        CORRECT                ADP                          z   
36        CORRECT                DET                    naszych   
37        CORRECT               NOUN                 samochodów   
38        CORRECT                ADP                         na   
39        CORRECT               NOUN                    terenie   
40        CORRECT              PROPN                   holandii   
41        CORRECT                ADP                          w   
42        CORRECT               NOUN                rotterdamie   
43        CORRECT              CCONJ                        czy   
44        CORRECT               VERB                 potwierdza   
45        CORRECT               NOUN                        pan   
46      INSERTION                                                 
47      INSERTION                                                 
48   SUBSTITUTION              SCONJ                         że   
49        CORRECT               VERB                  korzystał   
50   SUBSTITUTION               NOUN                        pan   
51   SUBSTITUTION                ADP                          z   
52        CORRECT               NOUN                      usług   
53   SUBSTITUTION               NOUN                    wynajmu   
54        CORRECT                ADP                          w   
55   SUBSTITUTION                DET                        tym   
56        CORRECT               NOUN                    miejscu   
57      INSERTION                                                 
58      INSERTION                                      

step_type        reference_word_text hypothesis_word_text
0    SUBSTITUTION                      dzień                   20
1    SUBSTITUTION                      dobry                   mb
2    SUBSTITUTION                    nazywam          grenadynami
3    SUBSTITUTION                        się                jeden
4    SUBSTITUTION                     dorota                    a
5    SUBSTITUTION                  pawłowska                    w
6    SUBSTITUTION                    dzwonię               każdym
7         CORRECT                          z                    z
8        DELETION               wypożyczalni                     
9        DELETION                 samochodów                     
10   SUBSTITUTION                       auto            opowiadań
11   SUBSTITUTION                dwadzieścia                    i
12   SUBSTITUTION                     cztery       prawdopodobnie
13   SUBSTITUTION                        czy                   do
14   SUBSTITUTION                  rozmawiam               dubaju
15   SUBSTITUTION                          z               cztery
16   SUBSTITUTION                      panem                 nowe
17        CORRECT                    arturem              arturem
18       DELETION                drzewieckim                     
19   SUBSTITUTION                      dzień          niemieckich
20   SUBSTITUTION                      dobry         intendentury
21        CORRECT                       panu                 panu
22        CORRECT                     bardzo               bardzo
23       DELETION                         mi                     
24   SUBSTITUTION                       miło              niemiła
25   SUBSTITUTION                    dzwonię                    <
26   SUBSTITUTION                         do                  unk
27   SUBSTITUTION                       pana                    >
28   SUBSTITUTION                          w               dłonie
29   SUBSTITUTION                    związku                   do
30   SUBSTITUTION                          z               upadku
31   SUBSTITUTION                   ostatnim                rządu
32   SUBSTITUTION              wypożyczeniem          pojmowaniem
33   SUBSTITUTION                    jednego               jednym
34        CORRECT                          z                    z
35        CORRECT                    naszych              naszych
36        CORRECT                 samochodów           samochodów
37        CORRECT                         na                   na
38        CORRECT                    terenie              terenie
39        CORRECT                   holandii             holandii
40        CORRECT                          w                    w
41        CORRECT                rotterdamie          rotterdamie
42        CORRECT                        czy                  czy
43        CORRECT                 potwierdza           potwierdza
44        CORRECT                        pan                  pan
45      INSERTION                                           tylko
46      INSERTION                                               i
47      INSERTION                                           opadł
48      INSERTION                                          buduje
49   SUBSTITUTION                         że             najmniej
50   SUBSTITUTION                  korzystał                    <
51   SUBSTITUTION                        pan                  unk
52   SUBSTITUTION                          z                    >
53   SUBSTITUTION                      usług                   do
54   SUBSTITUTION                    wynajmu                    <
55   SUBSTITUTION                          w                  unk
56   SUBSTITUTION                        tym                    >
57   SUBSTITUTION                    miejscu                    i
58   SUBSTITUTION                        mmh                    <
59   SUBSTITUTION                        już    

--------------------------------------------------------------
--------------------------------------------------------------
--------------------------------------------------------------


# Statistics of POS incorrect data

In [40]:
@dataclass
class AlignDetails:
    value_reference: Optional[str]
    value_hypothesis: Optional[str]
    
    @staticmethod
    def _get_string_or_default(value: Optional[str]) -> str:
        return value if value is not None else '___'
        
    def to_string(self) -> str:
        return f'{self._get_string_or_default(self.value_reference)} -> {self._get_string_or_default(self.value_hypothesis)}'
    
    def is_correct(self) -> bool:
        return self.value_reference == self.value_hypothesis
    
    
def get_align_details(repository_record: List[Any]) -> List[AlignDetails]:
    return [
        AlignDetails(
            value_reference=it['step_words']['reference_word']['text'] if 'reference_word' in it['step_words'] else None,
            value_hypothesis=it['step_words']['hypothesis_word']['text'] if 'hypothesis_word' in it['step_words'] else None
        )
        for it in repository_record
    ]


def show_stats(experiment_repository: ExperimentRepository, collections_config: CollectionsConfig):
    aggregated_aligned = [
        get_align_details(experiment_repository.get_property_for_key(record_id, collections_config.pos_asr_alignment_wer))
        for record_id in list(experiment_repository.get_all_record_ids())[:]
    ]
    list_of_aligns = list(itertools.chain(*aggregated_aligned))
    list_of_changes = [it.to_string() for it in list_of_aligns if not it.is_correct()]
    unique = np.unique(np.array(list_of_changes), return_counts=True)
    return pd.DataFrame({'values': unique[0], 'counts': unique[1]}).sort_values(by=['counts'], ascending=False).head(16)

# Luna Techmo

In [41]:
show_stats(luna_experiment_repository, techmo_connections_config)

values  counts
131     NUM -> ___    2290
192   PUNCT -> ___    1479
114    NOUN -> ___    1204
169  PROPN -> NOUN    1177
45      ADV -> ___    1073
30      ADP -> ___     988
246    ___ -> NOUN     918
130       NUM -> X     900
225    VERB -> ___     883
176   PROPN -> ___     823
162   PROPN -> ADJ     662
252    ___ -> VERB     632
161    PRON -> ___     613
146    PART -> ___     577
15      ADJ -> ___     560
73    CCONJ -> ___     495

## Luna AJN

In [42]:
show_stats(luna_experiment_repository, ajn_connections_config)

values  counts
284   ___ -> PUNCT    3344
256    VERB -> ___    1645
251  VERB -> PUNCT    1582
279    ___ -> NOUN    1548
28    ADP -> PUNCT    1522
52      ADV -> ___    1409
34      ADP -> ___    1316
124  NOUN -> PUNCT    1300
46    ADV -> PUNCT    1197
246   VERB -> NOUN    1186
41     ADV -> NOUN    1167
129    NOUN -> ___    1137
16      ADJ -> ___     879
162    PART -> ___     876
178    PRON -> ___     843
11    ADJ -> PUNCT     830

## VoiceLab Techmo

In [43]:
show_stats(voicelab_experiment_repository, techmo_connections_config)

values  counts
30     ADP -> ___    4527
121   NOUN -> ___    4129
151   PART -> ___    3585
167   PRON -> ___    3424
221   VERB -> ___    2935
46     ADV -> ___    2727
77   CCONJ -> ___    2360
135      NUM -> X    1842
136    NUM -> ___    1726
92     DET -> ___    1715
61     AUX -> ___    1634
204  SCONJ -> ___    1587
15     ADJ -> ___    1461
244   ___ -> NOUN    1251
250   ___ -> VERB    1178
119  NOUN -> VERB     677

## VoiceLab AJN

In [44]:
show_stats(voicelab_experiment_repository, ajn_connections_config)

values  counts
259    VERB -> ___   11609
140    NOUN -> ___   10416
53      ADV -> ___   10127
175    PART -> ___    9282
35      ADP -> ___    8663
192    PRON -> ___    8066
287   ___ -> PUNCT    6354
105     DET -> ___    6147
17      ADJ -> ___    5935
231   SCONJ -> ___    5385
254  VERB -> PUNCT    4842
134  NOUN -> PUNCT    4632
70      AUX -> ___    4016
249   VERB -> NOUN    3772
47    ADV -> PUNCT    3453
88    CCONJ -> ___    3438